In [ ]:
import os

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import norm, truncnorm, multivariate_normal
from sklearn.linear_model import LinearRegression

%matplotlib inline

In [ ]:
def positive_gauss(mean, std):
    rndnum = 0
    while rndnum <= 0:
        rndnum = random.gauss(mean, std)
    return rndnum

In [ ]:
def dist_trunc(mean,std,n):
    x_dist = truncnorm(a=-mean/std, b=np.inf,loc=mean,scale=std)
    return (x_dist.rvs(n)).astype(float)

In [ ]:
def dist_trunc_dep(meana,stda,meanb,stdb,covar,n):
    ref_matrix=np.array([[stda**2,covar],[covar,stdb**2]])
    ref_sample=multivariate_normal.rvs(mean=(meana,meanb),cov=ref_matrix, size=3*n)
    ref_sample = ref_sample[ref_sample[:,1] > 0]
    return ref_sample

In [ ]:
def find_q_sk(d,i):
    x=list()
    y=list()
    
    for k,v in d.items():
        a_ref_distrib_b_ref_distrib = d[k][0]['ref_alfa_dep'][i] / d[k][0]['ref_beta_dep'][i]
        
        for m,n in v.items():
            if m>0:
                a_div_a_ref_distrib =  d[k][m]['alfa'][i] /  d[k][0]['ref_alfa_dep'][i]                 
                y.append((a_div_a_ref_distrib-1.0)*a_ref_distrib_b_ref_distrib)
                x.append(d[k][m]['LET'])

    x= np.asarray(x).reshape(-1,1)
    reg = LinearRegression(fit_intercept=False).fit(x, y)
    q=reg.coef_[0]
    R=reg.score(x,y)
    return q,R

In [ ]:
num=100000

In [ ]:
fname = os.path.join('tmp','data_all.h5')
df = pd.read_hdf(fname, 'data')

In [ ]:
df2 = df.groupby(["article",'energy']).max()
df2.is_copy=False

\begin{align}
\frac{\alpha}{\alpha_{phot}} = 1+ \frac{q L}{(\frac{\alpha}{\beta})_{phot}}
\end{align}

In [ ]:
for name, group in df2.groupby('article'):
        for energy, data in group.groupby('energy'):
            if energy ==0:
                ab_ref=data["alfa(fit)/beta(fit)"].unique()                
                a_ref=data["alfa_fit"].unique()
                a_ref_err=data["alfa_fit_err"].unique()
                b_ref=data["beta_fit"].unique()
                b_ref_err=data["beta_fit_err"].unique()
                covar_ref= data["covar_fit"].unique()
                
                df2.loc[(name,energy),'a_fit_ref'] = a_ref
                df2.loc[(name,energy),'a_fit_ref_err'] = a_ref_err
                df2.loc[(name,energy),'b_fit_ref'] = b_ref
                df2.loc[(name,energy),'b_fit_ref_err'] = b_ref_err
                df2.loc[(name,energy),'covar_ref'] = covar_ref
            
            else:
                a=data["alfa_fit"].unique()
                a_err=data["alfa_fit_err"].unique()
                
                aa_ref=data['a(fit)/a_ref(fit)'].unique()
                aa_ref_art=data['a/a_ref'].unique()
                L=(data["LET"]).unique()
                
               
                q = (aa_ref-1.0)*ab_ref/L
                k=(aa_ref-1.0)/L

                
                error=  np.sqrt(np.power((1-a_ref)/b_ref*a_err,2)+
                                np.power((a-1)/b_ref*a_ref_err,2)+
                                np.power((a_ref-a)/np.power(b_ref,2)*b_ref_err,2))

                df2.loc[(name,energy),'q'] = q
                df2.loc[(name,energy),'k'] = k
                df2.loc[(name,energy), "error"] = error


In [ ]:
for name, group in df2.groupby('article'):
        for energy, data in group.groupby('energy'):
            df2.loc[(name, energy),"ab_ref"]=df2.loc[(name,0), "alfa(fit)/beta(fit)"]

In [ ]:
df2 = df2.replace([np.inf, -np.inf, np.NaN], 0)
df2.isnull().sum().sum()

## Drawing alpha & beta

In [ ]:
d ={}

In [ ]:
for name, group in df2.groupby('article'):
    d[name]={}
    for energy, data in group.groupby('energy'):
      
        if energy == 0:
            d[name][0] = {}
            d[name][0][ 'ref_alfa'] = dist_trunc(data.a_fit_ref.values, data.a_fit_ref_err.values, num)
            d[name][0][ 'ref_beta'] = dist_trunc(data.b_fit_ref.values, data.b_fit_ref_err.values, num)
            ref_sample = dist_trunc_dep(data.a_fit_ref.values.max(),data.a_fit_ref_err.values.max(),data.b_fit_ref.values.max(),data.b_fit_ref_err.values,data.covar_fit,num)
            d[name][0][ 'ref_alfa_dep']=ref_sample[:,0]
            d[name][0][ 'ref_beta_dep']=ref_sample[:,1]

        else:

            d[name][energy]={}
            d[name][energy][ 'alfa'] = dist_trunc(data.alfa_fit.values, data.alfa_fit_err.values, num)
            d[name][energy][ 'beta'] = dist_trunc(data.beta_fit.values, data.beta_fit_err.values, num)
            d[name][energy]['LET']=data.LET.values.max()
    

## Alpha & Beta distributions

In [ ]:
a = d['10'][1410]['alfa']
             
fiq,ax = plt.subplots()
                
weights = np.ones_like(a)/float(len(a))
bin_values,bin_edges, _= plt.hist(a, bins=100, alpha=0.5,weights=weights)

mean=np.asarray(a).mean()
plt.axvline(x=mean, label='mean α = {:.2f}'.format(mean),c='red',ls='--',lw=1.2)

plt.xlabel("α [1/Gy]",fontsize=13)
plt.legend( loc='best',ncol=1,  borderaxespad=0.)

plt.grid(b=True)              
plt.grid(which='minor', linestyle=':', linewidth='0.2', color='black')

plt.rcParams['xtick.direction'] = 'in' 
plt.rcParams['ytick.direction'] = 'in' 
plt.rcParams['xtick.top'] = True 
plt.rcParams['ytick.right'] = True
                
plt.savefig(fname="alpha_"+str(10)+"_"+str(1410)+".png",dpi=700)

df_tmp = pd.DataFrame()
df_tmp["bin_values"] = bin_values
df_tmp["alpha_left_edge"] = bin_edges[:-1]

df_tmp.to_csv("Alpha_10_1410")

In [ ]:
b=(d['10'][1410]['beta'])

fiq,ax = plt.subplots()

weights = np.ones_like(b)/float(len(b))
bina_values,bin_edges,_=plt.hist(b, bins=100, alpha=0.5,weights=weights)

mean=np.asarray(b).mean()
plt.axvline(x=mean, label='mean β = {:.2f}'.format(mean),c='red',ls='--',lw=1.2)

plt.xlabel("β [1/Gy^2]",fontsize=13)
plt.legend( loc='best',ncol=1,  borderaxespad=0.)
                
plt.grid()
plt.grid(which='minor', linestyle=':', linewidth='0.2', color='black')

plt.rcParams['xtick.direction'] = 'in' 
plt.rcParams['ytick.direction'] = 'in' 
plt.rcParams['xtick.top'] = True 
plt.rcParams['ytick.right'] = True

plt.savefig(fname="beta_"+str(10)+"__"+str(1410)+".png",dpi=700)

df_tmp = pd.DataFrame()
df_tmp["bin_values"] = bin_values
df_tmp["beta_left_edge"] = bin_edges[:-1]
df_tmp.to_csv("Beta_10_1410")

## Q-distribution

In [ ]:
qtmp,Rtmp=zip(*[find_q_sk(d,i) for i in range(num)])    

In [ ]:
R=pd.DataFrame(np.asarray(Rtmp))
qdf=pd.DataFrame(np.asarray(qtmp))
qdf.columns = ['q']

In [ ]:
qdf.median()

# Save


In [ ]:
hdf_fname = os.path.join('tmp','distrib_q.h5')
qdf.to_hdf(hdf_fname, 'q', format='table')